In [1]:
import json

In [2]:


experiments_path = "../"

def fc_to_string(k,cfg):
    res = f"k_{k}bits_"
    for layer in cfg:
        res += str(layer["bits"]) + "."
    
    res +=  "logsize_"
    for layer in cfg:
        res = res + str(layer["logsize"]) + "."
    
    return res


def bits_str(cfg):
    res = "b."
    for layer in cfg:
        res += str(layer["bits"]) + "."
    
    return res

def logsize_str(cfg):
    res = "sz."
    for layer in cfg:
        res = res + str(layer["logsize"]) + "."
    
    return res
  
def load_configs(name):
    with open(f'{experiments_path}config_{name}', 'r') as myfile:
        data=myfile.read()
        obj = json.loads(data)
        return obj["config"]  

def load_exp(fn):
    try:
        with open(fn, 'r') as myfile:
            data=myfile.read()
            # print(data)
            obj = json.loads(data)
            return obj
    except Exception as err:
        print(err)
        return None

    
polygon_sets = [("Us Zip Codes", "tl_2017_us_zcta510"), ("Global LSB", "Global_LSIB_Polygons_Detailed")]
datasets =[("Twitter 1 mio","twitter_1mio_coords.h5"), 
           ("Twitter 10 mio","twitter_10mio_coords.h5"),
           ("Twitter 100 mio","twitter_100mio_coords.h5"),
           ("Twitter 100 mio","twitter_100mio_coords.h5"),
           ("Asia 100 mio","asia_100mio_coords.h5"),
           ("Asia 200 mio","asia_200mio_coords.h5"),
           ("Asia 500 mio","asia_500mio_coords.h5"),
           ("Asia 1 bil","asia_1bil_coords.h5"),
          
          
          ]

In [3]:
k = 8;
x = 0;
width = 16 * 8192
height = 16 * 8192;
exp_name = "test_polygons";

cfgs = load_configs(exp_name)
print(len(cfgs))


432


In [4]:
import matplotlib.pyplot as plt
import matplotlib.ticker as ticker
import numpy as np
import matplotlib.backends.backend_pdf as pdf
import tqdm

def save_figs(fn):
    print(f"-->  Saving all figures... {fn}")
    out_pdf = pdf.PdfPages(fn)
    for fig in tqdm.tqdm(range(1, plt.gcf().number+1)):
        out_pdf.savefig( fig )
    out_pdf.close()
    plt.close("all")


def plot_matrix(cm, title='Experiment matrix', cmap='Greys', xlabels=None, ylabels=None, cblabel=None):
    fig = plt.figure(figsize=(len(xlabels)*1.25, 2+ len(ylabels)))
    ax = fig.add_subplot(111)
    # ax.xaxis.set_major_locator(ticker.MultipleLocator(2))
    # ax.yaxis.set_major_locator(ticker.MultipleLocator(1))
    cax = ax.matshow(cm,cmap=cmap)
    plt.title(title)
    ax.set_xticks(range(len(xlabels)))
    ax.set_yticks(range(len(ylabels)))
    cbar = fig.colorbar(cax)

    if cblabel:
        cbar.set_label(cblabel)
    if xlabels:
        ax.set_xticklabels(list(xlabels))
    if ylabels:
        ax.set_yticklabels(list(ylabels))
    plt.xlabel('Sizes')
    plt.ylabel('Bits')
    #plt.show()


def make_maps(size, cfgs):
    bits_map = {}
    logsize_map = {}
    numba = {}
    count_bits =0
    count_sizes = 0
    counter = 0
    for c in cfgs :

        if len(c) ==size:
            if(not bits_str(c) in bits_map):
                bits_map[bits_str(c)] = count_bits
                count_bits+=1
            if(not logsize_str(c) in logsize_map):
                logsize_map[logsize_str(c)] = count_sizes
                count_sizes+=1
        counter += 1
                
    return bits_map, logsize_map, numba

bits_map, logsize_map, numba = make_maps(2,cfgs)

print(len(bits_map), len(logsize_map), len(numba))
print(bits_map)
print(logsize_map)
print(numba)
a = np.random.rand(len(bits_map), len(logsize_map))
plot_matrix(a, ylabels=bits_map.keys(), xlabels=logsize_map.keys())


ValueError: too many values to unpack (expected 2)

In [ ]:
def make_matrices(size, cfgs):
    bits_map, logsize_map = make_maps(size,cfgs)
    matrices= {}
    matrix_indices = ["err_mean_pc"]
    for shapen,shapef in polygon_sets:
        matrices[shapef] = {}
        for dn, ds in datasets :
            matrices[shapef][ds] = {}
            for mi in matrix_indices:
                matrices[shapef][ds][mi] = np.zeros((len(bits_map),(len(logsize_map))))-1



    x=0
    for c in cfgs :
        # print(fc_to_string(k,c))
        y = 0;
        for shpn, shapef in polygon_sets:
            for  dn, ds in datasets :
                fn = experiments_path + exp_name + "/" + exp_name + f'.w{width}h{height}.{x:04d}.{y}-' + fc_to_string(k,c) \
                + ds + "." + shapef + ".json"
                # print(fn)
                data = load_exp(fn)
                bits = bits_str(c)
                sz = logsize_str(c)
                if data and bits in bits_map and  sz in logsize_map:
                    for mi in matrix_indices:
                        matrices[shapef][ds][mi][ bits_map[bits],logsize_map[sz]] = data[mi]
            y+=1
        x+=1

    for shpn, shapef in polygon_sets:
        for  dn, ds in datasets :
            for mi in matrix_indices:   
                plot_matrix( matrices[shapef][ds][mi] ,title=f'{dn} - {shpn}',ylabels=bits_map.keys(), xlabels=logsize_map.keys(), cblabel="% Error")             

make_matrices(1, cfgs)   
make_matrices(2, cfgs)              
make_matrices(3, cfgs)              


save_figs("polygons_test_matrices.pdf")

[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.asia_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.asia_200mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.asia_500mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.asia_1bil_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../t

[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0165.0-k_8bits_1.8.32.logsize_20.24.28.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0165.0-k_8bits_1.8.32.logsize_20.24.28.asia_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0165.0-k_8bits_1.8.32.logsize_20.24.28.asia_200mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0165.0-k_8bits_1.8.32.logsize_20.24.28.asia_500mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0165.0-k_8bits_1.8.32.logsize_20.24.28.asia_1bil_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0165.1-k_8bits_1.8.32.logsize_20.24.28.twitter_100mio_coords.h5.G

[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0338.0-k_8bits_8.16.64.logsize_28.16.20.asia_1bil_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0338.1-k_8bits_8.16.64.logsize_28.16.20.twitter_100mio_coords.h5.Global_LSIB_Polygons_Detailed.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0338.1-k_8bits_8.16.64.logsize_28.16.20.twitter_100mio_coords.h5.Global_LSIB_Polygons_Detailed.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0338.1-k_8bits_8.16.64.logsize_28.16.20.asia_100mio_coords.h5.Global_LSIB_Polygons_Detailed.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0338.1-k_8bits_8.16.64.logsize_28.16.20.asia_200mio_coords.h5.Global_LSIB_Polygons_Detailed.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0338.1-k_8bit

[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.asia_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.asia_200mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.asia_500mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.asia_1bil_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../t

[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0174.1-k_8bits_8.16.logsize_20.24.asia_500mio_coords.h5.Global_LSIB_Polygons_Detailed.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0174.1-k_8bits_8.16.logsize_20.24.asia_1bil_coords.h5.Global_LSIB_Polygons_Detailed.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0175.0-k_8bits_8.16.32.logsize_20.24.28.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0175.0-k_8bits_8.16.32.logsize_20.24.28.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0175.0-k_8bits_8.16.32.logsize_20.24.28.asia_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0175.0-k_8bits_8.16.32.logsize_20.24.28.asia_20

...

[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.asia_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.asia_200mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.asia_500mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.asia_1bil_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../t

[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0174.0-k_8bits_8.16.logsize_20.24.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0174.0-k_8bits_8.16.logsize_20.24.asia_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0174.0-k_8bits_8.16.logsize_20.24.asia_200mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0174.0-k_8bits_8.16.logsize_20.24.asia_500mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0174.0-k_8bits_8.16.logsize_20.24.asia_1bil_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0174.1-k_8bits_8.16.logsize_20.24.twitter_100mio_coords.h5.Global_LSIB_Polygons_Detailed.j

[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0345.0-k_8bits_1.8.32.logsize_28.16.24.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0345.0-k_8bits_1.8.32.logsize_28.16.24.asia_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0345.0-k_8bits_1.8.32.logsize_28.16.24.asia_200mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0345.0-k_8bits_1.8.32.logsize_28.16.24.asia_500mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0345.0-k_8bits_1.8.32.logsize_28.16.24.asia_1bil_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0345.1-k_8bits_1.8.32.logsize_28.16.24.twitter_100mio_coords.h5.G

-->  Saving all figures... polygons_test_matrices.pdf


100%|██████████| 48/48 [00:03<00:00, 15.51it/s]


In [ ]:
import numpy as np
import math
from matplotlib import pyplot as plt
import matplotlib.backends.backend_pdf as pdf
from mpl_toolkits.mplot3d import axes3d
figsize= (8,8)
def plot_hist(data, title="title", xlab="x", ylab="y", bins=20, log=False):
    plt.figure(figsize=figsize)
    bins = np.linspace(math.ceil(min(data)), 
                       math.floor(max(data)),
                       bins) # fixed number of bins

    plt.xlim([min(data)-5, max(data)+5])

    if(log):
        plt.hist(np.log10(data), bins=bins, alpha=0.5)
        
    else:
        plt.hist(data, bins=bins, alpha=0.5)
    plt.title(title)
    plt.xlabel(xlab)
    plt.ylabel(ylab)
    plt.show()

In [ ]:
from scipy import signal
from PIL import Image
def make_hist(size, cfgs):
    bits_map, logsize_map = make_maps(size,cfgs)
    matrices= {}
    matrix_indices = ["histogram_pc"]
    for shapen,shapef in polygon_sets:
        matrices[shapef] = {}
        for dn, ds in datasets :
            matrices[shapef][ds] = {}
            for mi in matrix_indices:
                matrices[shapef][ds][mi] = np.zeros((len(bits_map),(len(logsize_map))))-1



    x=0
    for c in cfgs :
        # print(fc_to_string(k,c))
        y = 0;
        for shpn, shapef in polygon_sets:
            for  dn, ds in datasets :
                fn = experiments_path + exp_name + "/" + exp_name + f'.w{width}h{height}.{x:04d}.{y}-' + fc_to_string(k,c) \
                + ds + "." + shapef + ".json"
                # print(fn)
                data = load_exp(fn)
                bits = bits_str(c)
                sz = logsize_str(c)
                if data and bits in bits_map and  sz in logsize_map:
                    for mi in matrix_indices:
                        p =  np.abs(data[mi]) #scipy.signal.resample(data[mi], 100)
                        ##p = np.array(Image.fromarray(data[mi]).resize(100,1))
                        #print(p)
                        plt.figure(figsize=figsize)
                        plt.bar(list(np.arange(0,100,100/len(p))),p)
                        plt.title(f'{dn} - {shpn} b{bits} sz{sz}')
                        #plt.show()

            y+=1
        x+=1

   # for shpn, shapef in polygon_sets:
   #     for  dn, ds in datasets :
   #         for mi in matrix_indices:   
   #             print(matrices[shapef][ds][mi])
make_hist(1,cfgs)
save_figs("polygons_test_hist1.pdf")
make_hist(2,cfgs)
save_figs("polygons_test_hist2.pdf")
make_hist(3,cfgs)
save_figs("polygons_test_hist3.pdf")

[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.asia_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.asia_200mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.asia_500mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0000.0-k_8bits_1.logsize_16.asia_1bil_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../t

[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0011.0-k_8bits_8.logsize_16.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0011.0-k_8bits_8.logsize_16.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0011.0-k_8bits_8.logsize_16.asia_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0011.0-k_8bits_8.logsize_16.asia_200mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0011.0-k_8bits_8.logsize_16.asia_500mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0011.0-k_8bits_8.logsize_16.asia_1bil_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../t

[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0018.0-k_8bits_1.logsize_16.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0018.0-k_8bits_1.logsize_16.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0018.0-k_8bits_1.logsize_16.asia_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0018.0-k_8bits_1.logsize_16.asia_200mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0018.0-k_8bits_1.logsize_16.asia_500mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0018.0-k_8bits_1.logsize_16.asia_1bil_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../t

[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0029.0-k_8bits_8.logsize_16.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0029.0-k_8bits_8.logsize_16.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0029.0-k_8bits_8.logsize_16.asia_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0029.0-k_8bits_8.logsize_16.asia_200mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0029.0-k_8bits_8.logsize_16.asia_500mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0029.0-k_8bits_8.logsize_16.asia_1bil_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../t

[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0036.0-k_8bits_1.logsize_16.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0036.0-k_8bits_1.logsize_16.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0036.0-k_8bits_1.logsize_16.asia_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0036.0-k_8bits_1.logsize_16.asia_200mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0036.0-k_8bits_1.logsize_16.asia_500mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0036.0-k_8bits_1.logsize_16.asia_1bil_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../t

...

[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0409.0-k_8bits_8.16.32.logsize_28.24.16.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0409.0-k_8bits_8.16.32.logsize_28.24.16.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0409.0-k_8bits_8.16.32.logsize_28.24.16.asia_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0409.0-k_8bits_8.16.32.logsize_28.24.16.asia_200mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0409.0-k_8bits_8.16.32.logsize_28.24.16.asia_500mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0409.0-k_8bits_8.16.32.logsize_28.24.16.asia_1bil_coord

[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0416.0-k_8bits_1.8.16.logsize_28.24.20.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0416.0-k_8bits_1.8.16.logsize_28.24.20.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0416.0-k_8bits_1.8.16.logsize_28.24.20.asia_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0416.0-k_8bits_1.8.16.logsize_28.24.20.asia_200mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0416.0-k_8bits_1.8.16.logsize_28.24.20.asia_500mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0416.0-k_8bits_1.8.16.logsize_28.24.20.asia_1bil_coords.h5.t

[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0420.0-k_8bits_1.16.32.logsize_28.24.20.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0420.0-k_8bits_1.16.32.logsize_28.24.20.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0420.0-k_8bits_1.16.32.logsize_28.24.20.asia_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0420.0-k_8bits_1.16.32.logsize_28.24.20.asia_200mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0420.0-k_8bits_1.16.32.logsize_28.24.20.asia_500mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0420.0-k_8bits_1.16.32.logsize_28.24.20.asia_1bil_coord

[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0427.0-k_8bits_8.16.32.logsize_28.24.20.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0427.0-k_8bits_8.16.32.logsize_28.24.20.twitter_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0427.0-k_8bits_8.16.32.logsize_28.24.20.asia_100mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0427.0-k_8bits_8.16.32.logsize_28.24.20.asia_200mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0427.0-k_8bits_8.16.32.logsize_28.24.20.asia_500mio_coords.h5.tl_2017_us_zcta510.json'
[Errno 2] No such file or directory: '../test_polygons/test_polygons.w131072h131072.0427.0-k_8bits_8.16.32.logsize_28.24.20.asia_1bil_coord

100%|██████████| 864/864 [00:56<00:00, 15.30it/s]
